In [3]:
import gradio as gr
import requests
from Bio.PDB import PDBParser
from gradio_molecule3d import Molecule3D
import numpy as np

# Function to fetch a PDB file from RCSB PDB
def fetch_pdb(pdb_id):
    pdb_url = f'https://files.rcsb.org/download/{pdb_id}.pdb'
    pdb_path = f'{pdb_id}.pdb'
    response = requests.get(pdb_url)
    if response.status_code == 200:
        with open(pdb_path, 'wb') as f:
            f.write(response.content)
        return pdb_path
    else:
        return None

# Function to process the PDB file and return random predictions
def process_pdb(pdb_id, segment):
    pdb_path = fetch_pdb(pdb_id)
    if not pdb_path:
        return "Failed to fetch PDB file", None, None

    parser = PDBParser(QUIET=True)
    structure = parser.get_structure('protein', pdb_path)
    
    try:
        chain = structure[0][segment]
    except KeyError:
        return "Invalid Chain ID", None, None

    sequence = [residue.get_resname() for residue in chain if residue.id[0] == ' ']
    random_scores = np.random.rand(len(sequence))

    result_str = "\n".join(
        f"{seq} {res.id[1]} {score:.2f}" 
        for seq, res, score in zip(sequence, chain, random_scores)
    )

    # Save the predictions to a file
    prediction_file = f"{pdb_id}_predictions.txt"
    with open(prediction_file, "w") as f:
        f.write(result_str)
    
    return result_str, pdb_path, prediction_file

#reps = [{"model": 0, "style": "cartoon", "color": "spectrum"}]

reps =    [
        {
          "model": 0,
          "style": "cartoon",
          "color": "whiteCarbon",
          "residue_range": "",
          "around": 0,
          "byres": False,
        },
        {
          "model": 0,
          "chain": "A",
          "resname": "HIS",
          "style": "stick",
          "color": "red"
        }
      ]


# Gradio UI
with gr.Blocks() as demo:
    gr.Markdown("# Protein Binding Site Prediction (Random Scores)")

    with gr.Row():
        pdb_input = gr.Textbox(value="2IWI", label="PDB ID", placeholder="Enter PDB ID here...")
        segment_input = gr.Textbox(value="A", label="Chain ID", placeholder="Enter Chain ID here...")
        visualize_btn = gr.Button("Visualize Structure")
        prediction_btn = gr.Button("Predict Random Binding Site Scores")

    molecule_output = Molecule3D(label="Protein Structure", reps=reps)
    predictions_output = gr.Textbox(label="Binding Site Predictions")
    download_output = gr.File(label="Download Predictions")

    visualize_btn.click(fetch_pdb, inputs=[pdb_input], outputs=molecule_output)
    prediction_btn.click(process_pdb, inputs=[pdb_input, segment_input], outputs=[predictions_output, molecule_output, download_output])

    gr.Markdown("## Examples")
    gr.Examples(
        examples=[
            ["2IWI", "A"],
            ["7RPZ", "B"],
            ["3TJN", "C"]
        ],
        inputs=[pdb_input, segment_input],
        outputs=[predictions_output, molecule_output, download_output]
    )

demo.launch()

* Running on local URL:  http://127.0.0.1:7862

To create a public link, set `share=True` in `launch()`.


In [2]:
import gradio as gr
import requests
from Bio.PDB import PDBParser
import numpy as np
import os
from gradio_molecule3d import Molecule3D

def read_mol(pdb_path):
    """Read PDB file and return its content as a string"""
    with open(pdb_path, 'r') as f:
        return f.read()

def fetch_pdb(pdb_id):
    pdb_url = f'https://files.rcsb.org/download/{pdb_id}.pdb'
    pdb_path = f'{pdb_id}.pdb'
    response = requests.get(pdb_url)
    if response.status_code == 200:
        with open(pdb_path, 'wb') as f:
            f.write(response.content)
        return pdb_path
    else:
        return None

def process_pdb(pdb_id, segment):
    pdb_path = fetch_pdb(pdb_id)
    if not pdb_path:
        return "Failed to fetch PDB file", None, None
    parser = PDBParser(QUIET=True)
    structure = parser.get_structure('protein', pdb_path)
    
    try:
        chain = structure[0][segment]
    except KeyError:
        return "Invalid Chain ID", None, None
    sequence = [residue.get_resname() for residue in chain if residue.id[0] == ' ']
    random_scores = np.random.rand(len(sequence))
    result_str = "\n".join(
        f"{seq} {res.id[1]} {score:.2f}" 
        for seq, res, score in zip(sequence, chain, random_scores)
    )
    # Save the predictions to a file
    prediction_file = f"{pdb_id}_predictions.txt"
    with open(prediction_file, "w") as f:
        f.write(result_str)
    
    return result_str, molecule(pdb_path, random_scores), prediction_file

def molecule(input_pdb, scores=None):
    mol = read_mol(input_pdb)  # Read PDB file content
    
    # Prepare high-scoring residues script if scores are provided
    high_score_script = ""
    if scores is not None:
        high_score_script = """
        // Highlight residues with high scores
        let highScoreResidues = [{}];
        viewer.getModel(0).setStyle(
            {{"resi": highScoreResidues}}, 
            {{"stick": {{"color": "red"}}}}
        );
        """.format(
            ", ".join(str(i+1) for i, score in enumerate(scores) if score > 0.8)
        )
    
    html_content = f"""
    <!DOCTYPE html>
    <html>
    <head>    
        <meta http-equiv="content-type" content="text/html; charset=UTF-8" />
        <style>
        .mol-container {{
            width: 100%;
            height: 700px;
            position: relative;
        }}
        </style>
        <script src="https://cdnjs.cloudflare.com/ajax/libs/jquery/3.6.3/jquery.min.js"></script>
        <script src="https://3Dmol.csb.pitt.edu/build/3Dmol-min.js"></script>
    </head>
    <body>
        <div id="container" class="mol-container"></div>
        <script>
            let pdb = `{mol}`; // Use template literal to properly escape PDB content
            $(document).ready(function () {{
                let element = $("#container");
                let config = {{ backgroundColor: "white" }};
                let viewer = $3Dmol.createViewer(element, config);
                viewer.addModel(pdb, "pdb");
                
                // Set cartoon representation with white carbon color scheme
                viewer.getModel(0).setStyle({{}}, {{ cartoon: {{ colorscheme:"whiteCarbon" }} }});
                
                {high_score_script}
                
                viewer.zoomTo();
                viewer.render();
                viewer.zoom(0.8, 2000);
            }});
        </script>
    </body>
    </html>
    """
    
    # Return the HTML content within an iframe safely encoded for special characters
    return f'<iframe width="100%" height="700" srcdoc="{html_content.replace(chr(34), "&quot;").replace(chr(39), "&#39;")}"></iframe>'

reps =    [
        {
          "model": 0,
          "style": "cartoon",
          "color": "whiteCarbon",
          "residue_range": "",
          "around": 0,
          "byres": False,
        }
    ]
# Gradio UI
with gr.Blocks() as demo:
    gr.Markdown("# Protein Binding Site Prediction (Random Scores)")
    with gr.Row():
        pdb_input = gr.Textbox(value="2IWI", label="PDB ID", placeholder="Enter PDB ID here...")
        segment_input = gr.Textbox(value="A", label="Chain ID", placeholder="Enter Chain ID here...")
        visualize_btn = gr.Button("Visualize Structure")
        #prediction_btn = gr.Button("Predict Random Binding Site Scores")

    molecule_output2 = Molecule3D(label="Protein Structure", reps=reps)

    with gr.Row():
        pdb_input = gr.Textbox(value="2IWI", label="PDB ID", placeholder="Enter PDB ID here...")
        segment_input = gr.Textbox(value="A", label="Chain ID", placeholder="Enter Chain ID here...")
        prediction_btn = gr.Button("Predict Random Binding Site Scores")

    molecule_output = gr.HTML(label="Protein Structure")
    predictions_output = gr.Textbox(label="Binding Site Predictions")
    download_output = gr.File(label="Download Predictions")
    
    #visualize_btn.click(
    #    fn=lambda pdb_id: molecule(fetch_pdb(pdb_id)), 
    #    inputs=[pdb_input], 
    #    outputs=molecule_output
    #)
    visualize_btn.click(fetch_pdb, inputs=[pdb_input], outputs=molecule_output2)
    
    
    prediction_btn.click(process_pdb, inputs=[pdb_input, segment_input], outputs=[predictions_output, molecule_output, download_output])
    
    gr.Markdown("## Examples")
    gr.Examples(
        examples=[
            ["2IWI", "A"],
            ["7RPZ", "B"],
            ["3TJN", "C"]
        ],
        inputs=[pdb_input, segment_input],
        outputs=[predictions_output, molecule_output, download_output]
    )

demo.launch()

* Running on local URL:  http://127.0.0.1:7860

To create a public link, set `share=True` in `launch()`.
